In [3]:
import pandas as pd
import numpy as np
import pybaseball


This block will download all of the raw data from 2017 through 2021


Some thoughts:
    I have two options:
        1) Download the data and cut it down/clean it to what it I want,
        2) Download the data, save that, then clean it and save that
        
        Option 1 is more memory efficient but option 1 is more time but 
        option 2 is more time efficient if/when I make mistakes
        
        So for now I'm going with option two and if that is super fast then I will
        delete that result and combine them into one script. Okay here goes

In [11]:
def get_data_from_mlb(start_year, end_year = None):
    
    if end_year == None:
        end_year = start_year + 1
    
    dfs = [] #https://github.com/jldbc/pybaseball/blob/master/EXAMPLES/imputed_derivation.ipynb
    for year in range(start_year, end_year + 1):
        print(f"Starting year {year}")
        dfs.append(pybaseball.statcast(start_dt=f'{year}-03-21', end_dt=f'{year}-12-01',verbose=False))
        #I'm overshooting the start and end here to make sure I don't miss anything
        #The statcast function is written in parallel, so that helps speed up this process
        
    # https://pandas.pydata.org/pandas-docs/stable/user_guide/merging.html
    print("Info succesfully downloaded from statcast")
    return pd.concat(dfs) 
    

In [13]:
if __name__ == '__main__':

    result = get_data_from_mlb(2017, 2021)
    
    folder_name = "data_files/"
    
    print("Writing raw data to csv")
    result.to_csv(folder_name + "raw_data_from_statcast.csv", index = False)
    
    
    
    key_points = result[[ 
                            "game_date",
                            "description",
                            "home_team",
                            "away_team",
                            "game_year",
                            "plate_x",
                            "plate_z",
                            "sz_top",
                            "sz_bot",
                            "game_pk"
    ]]
    
    print("Writing key_points data to csv")
    key_points.to_csv(folder_name + "key_points.csv", index = False)
    
    

Starting year 2017


100%|████████████████████████████████████████████████████████████████████████████████| 214/214 [00:33<00:00,  6.46it/s]


Starting year 2018


100%|████████████████████████████████████████████████████████████████████████████████| 214/214 [01:04<00:00,  3.32it/s]


Starting year 2019


...

Starting year 2020


100%|██████████████████████████████████████████████████████████████████████████████████| 97/97 [00:27<00:00,  3.57it/s]


Starting year 2021


100%|████████████████████████████████████████████████████████████████████████████████| 240/240 [01:05<00:00,  3.64it/s]


Info succesfully downloaded from statcast
Writing raw data to csv
Writing key_points data to csv


key_points.csv has all of the pitch information I need to work with. 

Now I need to group them by game, and rate the ump's performance for that game

In [1]:
class Rate_Game:
    """
    Inputs:
        game_df: 
            pandas df of all of the pitches 
            In most cases this will be one game, but I guess I could use this to get overall averages too
        game_pk:
            ID of the game
    Output:
        A pandas series that will have the following information:
        game_pk, game_date, ump accuracy, ump consistency
    """
    
    def grade_game(game_df, game_pk):
        sz_L = -.8308
        sz_R = .8308

        #https://stackoverflow.com/questions/30631841/pandas-how-do-i-assign-values-based-on-multiple-conditions-for-existing-columns
        game_df["accurate"] = np.where(
            (game_df["plate_x"] > sz_L) & \
            (game_df["plate_x"] < sz_R) & \
            (game_df["plate_z"] > game_df["sz_bot"]) & \
            (game_df["plate_z"] < game_df["sz_top"]),
            True, False
        ) 

        #Now we need to figure out consistency
        #Then build & return the series

        print(game_df)
        exit()


In [4]:
key_points = pd.read_csv("data_files/key_points.csv")
game_groups = key_points.groupby(['game_pk'])

In [ ]:
game_groups = key_points.groupby(['game_pk'])
for game_pk, game_df in game_groups.__iter__(): #iters through every game
    #print(game_df)
    Rate_Game.grade_game(game_df, game_pk)


    exit()

         game_date      description home_team away_team  game_year  plate_x  \
731276  2017-04-03    hit_into_play       NYM       ATL       2017     0.19   
731277  2017-04-03             foul       NYM       ATL       2017     0.81   
731278  2017-04-03             ball       NYM       ATL       2017     1.10   
731279  2017-04-03             ball       NYM       ATL       2017     1.38   
731280  2017-04-03  swinging_strike       NYM       ATL       2017     1.27   
...            ...              ...       ...       ...        ...      ...   
731559  2017-04-03    hit_into_play       NYM       ATL       2017    -0.77   
731560  2017-04-03             ball       NYM       ATL       2017     0.00   
731561  2017-04-03  swinging_strike       NYM       ATL       2017     1.20   
731562  2017-04-03             foul       NYM       ATL       2017    -0.14   
731563  2017-04-03             foul       NYM       ATL       2017     0.15   

        plate_z  sz_top  sz_bot  game_pk  accurate 

[353 rows x 11 columns]
         game_date      description home_team away_team  game_year  plate_x  \
722851  2017-04-05    hit_into_play       LAD        SD       2017    -0.02   
722852  2017-04-05  swinging_strike       LAD        SD       2017     0.20   
722853  2017-04-05  swinging_strike       LAD        SD       2017     0.49   
722854  2017-04-05             ball       LAD        SD       2017     0.03   
722855  2017-04-05  swinging_strike       LAD        SD       2017    -0.04   
...            ...              ...       ...       ...        ...      ...   
723104  2017-04-05             ball       LAD        SD       2017    -0.89   
723105  2017-04-05             ball       LAD        SD       2017     0.23   
723106  2017-04-05             ball       LAD        SD       2017     1.00   
723107  2017-04-05             ball       LAD        SD       2017     1.49   
723108  2017-04-05    called_strike       LAD        SD       2017    -0.18   

        plate_z  sz_top  sz

         game_date      description home_team away_team  game_year  plate_x  \
713328  2017-04-08    called_strike       DET       BOS       2017     0.34   
713329  2017-04-08    called_strike       DET       BOS       2017     0.82   
713330  2017-04-08         foul_tip       DET       BOS       2017     0.30   
713331  2017-04-08         foul_tip       DET       BOS       2017     0.49   
713332  2017-04-08             foul       DET       BOS       2017    -0.85   
...            ...              ...       ...       ...        ...      ...   
713599  2017-04-08  swinging_strike       DET       BOS       2017    -0.07   
713600  2017-04-08    called_strike       DET       BOS       2017    -0.30   
713601  2017-04-08             ball       DET       BOS       2017    -1.81   
713602  2017-04-08    called_strike       DET       BOS       2017     0.26   
713603  2017-04-08             ball       DET       BOS       2017    -0.96   

        plate_z  sz_top  sz_bot  game_pk  accurate 

[347 rows x 11 columns]
         game_date      description home_team away_team  game_year  plate_x  \
702183  2017-04-10  swinging_strike       NYY        TB       2017     1.26   
702184  2017-04-10  swinging_strike       NYY        TB       2017     0.26   
702185  2017-04-10             foul       NYY        TB       2017    -0.43   
702186  2017-04-10             ball       NYY        TB       2017     1.25   
702187  2017-04-10             ball       NYY        TB       2017    -0.77   
...            ...              ...       ...       ...        ...      ...   
702401  2017-04-10             ball       NYY        TB       2017    -1.75   
702402  2017-04-10             ball       NYY        TB       2017     0.41   
702403  2017-04-10             foul       NYY        TB       2017    -1.07   
702404  2017-04-10    called_strike       NYY        TB       2017    -0.40   
702405  2017-04-10    hit_into_play       NYY        TB       2017     0.02   

        plate_z  sz_top  sz

         game_date      description home_team away_team  game_year  plate_x  \
691726  2017-04-13    hit_into_play       MIA       NYM       2017     0.25   
691727  2017-04-13  swinging_strike       MIA       NYM       2017    -0.50   
691728  2017-04-13             ball       MIA       NYM       2017    -2.86   
691729  2017-04-13             ball       MIA       NYM       2017    -1.28   
691730  2017-04-13             foul       MIA       NYM       2017    -0.65   
...            ...              ...       ...       ...        ...      ...   
692230  2017-04-13             ball       MIA       NYM       2017     1.15   
692231  2017-04-13  swinging_strike       MIA       NYM       2017     0.43   
692232  2017-04-13             foul       MIA       NYM       2017    -0.41   
692233  2017-04-13    called_strike       MIA       NYM       2017    -0.07   
692234  2017-04-13    hit_into_play       MIA       NYM       2017    -0.51   

        plate_z  sz_top  sz_bot  game_pk  accurate 

...

[304 rows x 11 columns]
         game_date      description home_team away_team  game_year  plate_x  \
939536  2018-08-12  swinging_strike       DET       MIN       2018     0.46   
939537  2018-08-12             foul       DET       MIN       2018    -0.55   
939538  2018-08-12             foul       DET       MIN       2018    -0.55   
939539  2018-08-12             foul       DET       MIN       2018    -0.27   
939540  2018-08-12             ball       DET       MIN       2018     2.11   
...            ...              ...       ...       ...        ...      ...   
939782  2018-08-12    hit_into_play       DET       MIN       2018    -1.00   
939783  2018-08-12             ball       DET       MIN       2018     3.52   
939784  2018-08-12             foul       DET       MIN       2018    -0.63   
939785  2018-08-12             ball       DET       MIN       2018     1.76   
939786  2018-08-12    called_strike       DET       MIN       2018    -0.07   

        plate_z  sz_top  sz

         game_date      description home_team away_team  game_year  plate_x  \
929078  2018-08-15    hit_into_play       PHI       BOS       2018     0.01   
929079  2018-08-15             ball       PHI       BOS       2018    -2.00   
929080  2018-08-15  swinging_strike       PHI       BOS       2018     0.05   
929081  2018-08-15             foul       PHI       BOS       2018    -0.85   
929082  2018-08-15             ball       PHI       BOS       2018     0.97   
...            ...              ...       ...       ...        ...      ...   
929378  2018-08-15    hit_into_play       PHI       BOS       2018    -0.40   
929379  2018-08-15         foul_tip       PHI       BOS       2018     0.22   
929380  2018-08-15             ball       PHI       BOS       2018    -1.46   
929381  2018-08-15             foul       PHI       BOS       2018     0.56   
929382  2018-08-15    called_strike       PHI       BOS       2018    -0.82   

        plate_z  sz_top  sz_bot  game_pk  accurate 

[286 rows x 11 columns]
         game_date      description home_team away_team  game_year  plate_x  \
918110  2018-08-17    hit_into_play       BOS        TB       2018    -0.03   
918111  2018-08-17             ball       BOS        TB       2018     1.09   
918112  2018-08-17  swinging_strike       BOS        TB       2018    -0.06   
918113  2018-08-17  swinging_strike       BOS        TB       2018     0.18   
918114  2018-08-17    hit_into_play       BOS        TB       2018    -1.11   
...            ...              ...       ...       ...        ...      ...   
918378  2018-08-17    hit_into_play       BOS        TB       2018     0.39   
918379  2018-08-17             foul       BOS        TB       2018    -0.21   
918380  2018-08-17             foul       BOS        TB       2018     0.71   
918381  2018-08-17    hit_into_play       BOS        TB       2018     0.27   
918382  2018-08-17             ball       BOS        TB       2018    -0.64   

        plate_z  sz_top  sz

         game_date      description home_team away_team  game_year  plate_x  \
909000  2018-08-19    hit_into_play       NYY       TOR       2018    -0.13   
909001  2018-08-19             ball       NYY       TOR       2018     0.17   
909002  2018-08-19             foul       NYY       TOR       2018     0.16   
909003  2018-08-19    called_strike       NYY       TOR       2018     0.22   
909004  2018-08-19             ball       NYY       TOR       2018     0.33   
...            ...              ...       ...       ...        ...      ...   
909322  2018-08-19  swinging_strike       NYY       TOR       2018     0.04   
909323  2018-08-19             foul       NYY       TOR       2018     1.09   
909324  2018-08-19    hit_into_play       NYY       TOR       2018    -0.61   
909325  2018-08-19             ball       NYY       TOR       2018     1.81   
909326  2018-08-19             foul       NYY       TOR       2018    -0.08   

        plate_z  sz_top  sz_bot  game_pk  accurate 

[324 rows x 11 columns]
         game_date      description home_team away_team  game_year  plate_x  \
898337  2018-08-22    hit_into_play       WSH       PHI       2018     0.24   
898338  2018-08-22     blocked_ball       WSH       PHI       2018     1.50   
898339  2018-08-22    called_strike       WSH       PHI       2018    -0.27   
898340  2018-08-22             ball       WSH       PHI       2018    -1.07   
898341  2018-08-22    hit_into_play       WSH       PHI       2018     0.08   
...            ...              ...       ...       ...        ...      ...   
898666  2018-08-22    called_strike       WSH       PHI       2018    -0.67   
898667  2018-08-22  swinging_strike       WSH       PHI       2018     0.17   
898668  2018-08-22             ball       WSH       PHI       2018     1.38   
898669  2018-08-22             ball       WSH       PHI       2018     0.76   
898670  2018-08-22    called_strike       WSH       PHI       2018     0.20   

        plate_z  sz_top  sz